
# Phenomonological analysis of $B\to D^{(*)} \ell \nu$ decays using EOS

<center><img src="files/github-eos-logo.png"/></center>

**Méril Reboud** (<span style="color: #68246D">IPPP Durham</span>)<br/> on behalf of the EOS collaboration<br/>

You can find a list of all contributors <a href="https://eos.github.io/">here</a>

### What you will learn:
 1. How to setup a simple Bayesian analysis in EOS, including finding the relevant observables, statistical constraints, and options;
 2. How to "run" the analysis, i.e. get the fit quality and produce posterior samples;
 3. How to extract parameters and predict observables including uncertainties.

### What you will not learn:
 - How to extend EOS with new observables (described [here](https://eos.github.io/doc/defining-observables.html))
 - How to simulate a decay (described [here](https://eos.github.io/doc/simulation.html))

## Analysis skeleton

All analyses follow the same recipe:
 1. Define the parameters of interest
 2. Find all the relevant nuisance parameters
 3. Define the experimental and theoretical constraints
 4. Test your fit model, and sample from the posterior(s)
 5. Interpret the posterior(s), extract parameter values, predict observables...


**Aim of this hands-on tutorial**:
Extract $V_{cb}$ from branching ratio measurements of $B \to D^{(*)} \ell \bar{\nu}$ decays.


## 1. Parameter(s) of Interest

The list of parameters can be scanned interactively using `eos.Parameters` or on the <a href="https://eos.github.io/doc/parameters.html">online documentation</a> (you can also have a look at the [EOS paper](https://arxiv.org/pdf/2111.15428.pdf)).

In [ ]:
import eos
eos.Parameters(name="V_cb")

In this tutorial we will focus on `CKM::abs(V_cb)`.

See how EOS handles names following the scheme:
``
PREFIX::NAME[@SUFFIX][;OPTIONLIST]
``.

## 2. Nuisance parameters

This is the main step because it requires some assumptions on the theory description of the data. As you have learned earlier today, the main source of uncertainties is due to our limited knowledge of the form factors describing the hadronic transitions.

In this tutorial we will use the BGL parameterization, and start with a truncation order `N = 1`. We write the form factors as: $$f_i(q^2) = \text{known functions} \times \sum_{n=0}^N \color{\red}{a^{(i)}_n} z^n(q^2) \,.$$

The `known functions` are such that the parameters $\color{\red}{a^{(i)}_n}$ follow the *dispersive bounds* (one per current):
    $$\sum_{n=0}^N \left| \color{\red}{a^{(i)}_n} \right|^2 < 1$$

In [ ]:
eos.Parameters(prefix="B->D", suffix="BGL")

  - In the SM, the tensor form factors ($f_T, T_1, T_2, T_{23}$) don't play any role. They are only needed for BSM analyses.
  - The parameters `B->D^*::a^F1_0@BGL1997` and `B->D^*::a^F2_0@BGL1997` are constrained by theory relations and can therefore be removed from the priors.

## 3. Constraints

We have three types of constraints:

  1. Experimental measurements of the branching ratios
  2. Lattice estimates of the form factors
  3. Dispersive bounds

In [ ]:
eos.Constraints(prefix="->D", name="BR")

In [ ]:
eos.Constraints(prefix="->D", suffix="FNAL+MILC")

In [ ]:
eos.Constraints(prefix="->D", suffix="HPQCD")

The dispersive bounds are not available in EOS' database of constraints, we will manually create them:

In [ ]:
eos.Observables(prefix="b->c", suffix="BGL")

```
'b->c::Bound[0^+]':
    type: UniformBound
    observables:
        - b->c::Bound[0^+]@BGL
    kinematics: [ {} ]
    options: [ {"z-order-bound": "1"} ]
    bound: 1.0
    uncertainty: 0.1
```

## A bit of organization

In order to:
 - reproduce, share and modify analyses,
 - perform several analyses that share priors / constraints, etc...

EOS allows to write all the analysis in a separate <span style="color: #68246D">analysis file</span>. This YAML file collects all the necessary information, i.e.:

`priors`
: all the varied parameters and their distributions

`likelihoods`
: the theoretical and experimental constraints

`posteriors`
: the specification for you analysis, which prior to use, what are the global options...

`predictions`
: an optional field to specify what to predict with the samples

```
priors:
  - name: Vcb
    descriptions:
     - {'parameter': 'CKM::abs(V_cb)', 'min': XXX, 'max': YYY, 'type': 'uniform'}
```

```
likelihoods:
  - name: BToD-BR
    constraints:
      - B^0->D^+mu^-nu::BRs@Belle:2015A
```

```
posteriors:
  - name: Vcb-only
    global_options:
      model: CKM
      form-factors: BGL1997
    prior:
      - Vcb
    likelihood:
      - BToD-BR
```

## Your turn #1

(30') Fill the analysis file `Vcb_tutorial.yaml` with all the necessary information:
 - You can use the commands collected in this notebook
 - For the prior ranges, use physically or theoretically allowed ranges.
 - Write a posterior with $B\to D$ contraints only and one including all the constraints
 - You can test your analysis file by loading it with `eos.AnalysisFile($file)`

## 4. Test of the model and sampling

In [ ]:
BASE_DIRECTORY = !pwd
BASE_DIRECTORY = BASE_DIRECTORY[0]

file = BASE_DIRECTORY + '/Vcb_tutorial_filled.yaml'
af = eos.AnalysisFile(file)

In [ ]:
posterior = 'BToD-BGL2' #'global-BGL2'
analysis = af.analysis(posterior)

### 4.1 Sample from the posterior

There exist many sampling algorithms: MCMC, PMC...
In this tutorial we will use Nested Sampling since it is very close to a black box.

Sample from the $B\to D$-only posterior and import the results:

In [ ]:
resample = False
if resample:
    eos.tasks.sample_nested(file, posterior)

importance_samples = eos.data.ImportanceSamples(BASE_DIRECTORY + '/' + posterior + '/samples')
print(f"Collected {f.samples.shape[0]} samples")

In [ ]:
!tree $BASE_DIRECTORY/$posterior

The global $B\to D^{(*)}$ sampling takes ~60 minutes on my laptop, ~15 minutes on a 32 cores machine.

### 4.2 Optimize the posterior and test the model

EOS optimization is based on [scipy.optimize](https://docs.scipy.org/doc/scipy/reference/optimize.html). We start optimization from the most likely candidate found during the sampling process.

In [ ]:
bfp, gof = eos.tasks.find_mode(af, posterior, base_directory=BASE_DIRECTORY, importance_samples = True)

In [ ]:
display(gof)

In [ ]:
!tree $BASE_DIRECTORY/$posterior

## 5. Interpret, Plot and Predict

### 5.1 The plotting framework

EOS implements a matplotlib-based plotting framework.
Several contents are supported:
 - constraints
 - observables
 - observables with uncertainty bands
 - ... see [here](https://eos.github.io/doc/api/python.html#module-eos-plot) for the complete list

In [ ]:
plot_args = {
    'plot': {
        'x': { 'label': r'$q^2$', 'unit': r'$\textnormal{GeV}^2$',  'range': [-2, 14] },
        'y': { 'label': r'form factor', 'range': [0, 2]  },
        'legend': { 'location': 'upper left' }
    },
    'contents': [
        { 'label': r'HPQCD 2015', 'type': 'constraint',
          'constraints': 'B->D::f_++f_0@HPQCD:2015A', 'observable': 'B->D::f_+(q2)',
          'variable': 'q2'},
        { 'label': r'FNAL+MILC 2015', 'type': 'constraint',
          'constraints': 'B->D::f_++f_0@FNAL+MILC:2015B', 'observable': 'B->D::f_+(q2)',
          'variable': 'q2'},
        { 'label': r'$f_+^{B\to D}$', 'type': 'observable',
          'observable': 'B->D::f_+(q2);form-factors=BGL1997', 'variable': 'q2',
          'parameters-from-mode': BASE_DIRECTORY + "/" + posterior + "/mode-default/" },
    ]
}
plot = eos.plot.Plotter(plot_args).plot()

### 5.2 Predictions

To complete the analysis automatization, the analysis file also accepts a `predictions` item.

```
predictions:
  - name: BToDstar-BR
    observables:
      - { name: 'B->D^*lnu::BR;l=e,q=d',
          kinematics: { 'q2_min': 0.3e-7, 'q2_max': 11.658 } }
      - { name: 'B->D^*lnu::BR;l=e,q=u',
          kinematics: { 'q2_min': 0.3e-7, 'q2_max': 11.628 } }
```

In [ ]:
eos.tasks.predict_observables(af, posterior, "BToDstar-BR", base_directory=BASE_DIRECTORY)

In [ ]:
!tree $BASE_DIRECTORY/$posterior

In [ ]:
BToDstarBRs = eos.Prediction(BASE_DIRECTORY + "/" + posterior + "/pred-BToDstar-BR")

import numpy as np
np.average(BToDstarBRs.samples, weights=BToDstarBRs.weights, axis=0)

## Your turn #2

  1. (10') Extract $|V_{cb}|$ from the weighted samples, visualize the posterior distribution, compare it to some world average.
  2. (5') Compute the saturation of the dispersive bounds. What role do they play in your extraction of $V_{cb}$?
  3. (40') Using EOS' plotting framework, visualize the form factors and the branching ratios (use `'type': 'uncertainty'` in EOS' plotting framework, as described [here](https://eos.github.io/doc/api/python.html#plotting-uncertainty-bands))
  4. (30') Predict angular observables for $B \to D^* \ell \bar{\nu}$ decays and compare them to the latest measurements.

## To go further

  - How can we quantify the impact of the truncation order $N$?
  - Is there any room for new physics in $B \to D^{(*)} \ell \bar{\nu}$ decays?